In [1]:
from flask import Flask, render_template, request, jsonify
from flask_cors import CORS, cross_origin
from selenium.webdriver.chrome.options import Options
from urllib.request import urlopen as uReq
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager
from bs4 import BeautifulSoup as bs
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import time
import os
import re
import pandas as pd

In [2]:
import logging

# Create logs folder if it doesn't exist
os.makedirs("logs", exist_ok=True)

# Configure logging
logging.basicConfig(
    filename="logs/app.log",  # Log file location
    level=logging.INFO,  # Set logging level (DEBUG, INFO, WARNING, ERROR, CRITICAL)
    format="%(asctime)s - %(levelname)s - %(message)s",
    datefmt="%Y-%m-%d %H:%M:%S"
)

# Add a console handler (optional, for printing logs to terminal)
console_handler = logging.StreamHandler()
console_handler.setLevel(logging.INFO)  # Change to DEBUG for more details
console_handler.setFormatter(logging.Formatter("%(asctime)s - %(levelname)s - %(message)s"))
logging.getLogger().addHandler(console_handler)

logging.info("Logging is set up.")


2025-03-08 20:02:33,699 - INFO - Logging is set up.


In [3]:
options = webdriver.ChromeOptions()
options.add_argument("--headless")  # Run Chrome in headless mode
service = Service('/home/aditya/Documents/IITK_SEM/SEM_2/661/Project/chromedriver-linux64/chromedriver')
browser = webdriver.Chrome(service=service, options=options)

# Monthly

In [4]:
file_path = "dir_names.txt"  # Ensure this file exists

directory_name = []
with open(file_path, "r") as file:
    directory_name = [line.strip() for line in file]

master_formatted_train_name = []

columns = ["Train_No", "Train_Name", "Station_Name", "Station_Code", "Delay", "Zone"]
df_master = pd.DataFrame(columns=columns)
df_master["Train_No"] = df_master["Train_No"].astype(str)  # Ensure "Train_No" remains a string

t_no=1

for folder in directory_name:
    formatted_train_names = []
    file_path = os.path.join(folder, "fomatted_links.txt")  # Construct file path
    df_category = pd.DataFrame(columns=columns)
    df_category["Train_No"] = df_category["Train_No"].astype(str)  # Ensure "Train_No" remains a string
    i=int(1)
    
    try:
        with open(file_path, "r") as file:
            for line in file: # For each train in that category
                try:
                    print(f"Processing folder {folder} Train Serial No {t_no} : link = {line}")
                    t_no += 1
                    browser.get(line)
                    elements = browser.find_elements(By.CSS_SELECTOR, "td.left.pud3")
                    del elements[1:2]
                    elements.pop()
                    match = re.search(r"Running History of (.+?) \((\d{5})\)", elements[0].text)

                    if match:
                        train_name = match.group(1)  # Extracts the name
                        train_number = str(match.group(2))  # Extracts the number

                    df_train = pd.DataFrame(columns=columns)
                    df_train["Train_No"] = df_train["Train_No"].astype(str)  # Ensure "Train_No" remains a string

                    if(elements[1].text == "Historical running data of queried train for selected duration is not available."):
                        df_train.loc[len(df_train)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                        df_category.loc[len(df_category)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                        df_master.loc[len(df_master)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                    else:
                        del elements[0]
                        sub_elements=elements[0].find_elements(By.CLASS_NAME, "runStatStn")
                        rows = browser.find_elements(By.CSS_SELECTOR, "tr.even.dborder")
                        td_element=rows[2].find_elements(By.CSS_SELECTOR, "td[colspan]")[0].text
                        match = re.search(r"Zone:\s*([A-Z]+)", td_element)
                        zone = match.group(1)  # Extracted zone code

                        for sub_element in sub_elements:
                            class_value = sub_element.get_attribute("class")  # Get full class attribute
                            
                            if "runStatStn blocklink rnd5" in class_value:  # Ensure full class match
                                match = re.search(r"([\w\s]+) \((\w+)\)\s*\nAvg\. Delay: (\d+) Min", sub_element.text)

                                if match:
                                    station_name = match.group(1)  # "KANPUR CENTRAL"
                                    station_code = match.group(2)  # "CNB"
                                    delay = match.group(3)         # "56"

                                    df_train.loc[len(df_train)] = [train_number, train_name, station_name, station_code, delay, zone]
                                    df_category.loc[len(df_category)] = [train_number, train_name, station_name, station_code, delay, zone]
                                    df_master.loc[len(df_master)] = [train_number, train_name, station_name, station_code, delay, zone]

                    save_folder = os.path.join(folder, "Monthly_Delay")

                    os.makedirs(save_folder, exist_ok=True)  # Creates "Monthly" inside "folder" if not present

                    save_file_train = os.path.join(save_folder, f"{i}_{train_number}_Monthly_Delay.csv")
                    df_train.to_csv(save_file_train, index=False)  # Saves without index
                    i+=1
                except Exception as e:
                    logging.error(f"Error occurred: {e} in processing link {line}", exc_info=True)  # Logs full traceback

        save_file_cat = os.path.join(folder, "Category_Monthly_Delay.csv")
        df_category.to_csv(save_file_cat, index=False)  # Saves without index
    except Exception as e:
        logging.error(f"Error occurred: {e} in category {folder}", exc_info=True)  # Logs full traceback
    
save_folder = "Master_Delay"
os.makedirs(save_folder, exist_ok=True)
Master_Monthly_Delay_Save = os.path.join(save_folder, "Master_Monthly_Delay.csv")
df_master.to_csv(Master_Monthly_Delay_Save, index=False)

Processing folder List_of_All_Rajdhani_Trains Train Serial No 1 : link = https://etrain.info/train/Nzm-Rajdhani-Spl-01221/history

Processing folder List_of_All_Rajdhani_Trains Train Serial No 2 : link = https://etrain.info/train/Csmt-Rajdni-Spl-01222/history

Processing folder List_of_All_Rajdhani_Trains Train Serial No 3 : link = https://etrain.info/train/Tvc-Nzm-Raj-Exp-02431/history

Processing folder List_of_All_Rajdhani_Trains Train Serial No 4 : link = https://etrain.info/train/Nzm-Tvc-Raj-Spl-02432/history

Processing folder List_of_All_Rajdhani_Trains Train Serial No 5 : link = https://etrain.info/train/Ndls-Rnc-Spl-02454/history

Processing folder List_of_All_Rajdhani_Trains Train Serial No 6 : link = https://etrain.info/train/Kolkata-Rajdhni-12301/history

Processing folder List_of_All_Rajdhani_Trains Train Serial No 7 : link = https://etrain.info/train/Kolkata-Rjdhni-12302/history

Processing folder List_of_All_Rajdhani_Trains Train Serial No 8 : link = https://etrain.info/

2025-03-08 20:11:37,612 - ERROR - Error occurred: pop from empty list in processing link https://etrain.info/train/Rmr-Cdg-Sf-Exp-12527/history
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/2248691922.py", line 31, in <module>
    elements.pop()
    ~~~~~~~~~~~~^^
IndexError: pop from empty list
2025-03-08 20:11:37,698 - ERROR - Error occurred: pop from empty list in processing link https://etrain.info/train/Cdg-Rmr-Sf-Exp-12528/history
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/2248691922.py", line 31, in <module>
    elements.pop()
    ~~~~~~~~~~~~^^
IndexError: pop from empty list


Processing folder List_of_All_Superfast_Trains Train Serial No 1324 : link = https://etrain.info/train/Rmr-Cdg-Sf-Exp-12527/history

Processing folder List_of_All_Superfast_Trains Train Serial No 1325 : link = https://etrain.info/train/Cdg-Rmr-Sf-Exp-12528/history

Processing folder List_of_All_Superfast_Trains Train Serial No 1326 : link = https://etrain.info/train/Ppta-Ljn-Sf-Exp-12529/history

Processing folder List_of_All_Superfast_Trains Train Serial No 1327 : link = https://etrain.info/train/Ljn-Ppta-Sf-Exp-12530/history

Processing folder List_of_All_Superfast_Trains Train Serial No 1328 : link = https://etrain.info/train/Pushpak-Express-12533/history

Processing folder List_of_All_Superfast_Trains Train Serial No 1329 : link = https://etrain.info/train/Pushpak-Express-12534/history

Processing folder List_of_All_Superfast_Trains Train Serial No 1330 : link = https://etrain.info/train/Manduadih-Exp-12537/history

Processing folder List_of_All_Superfast_Trains Train Serial No 133

# Weekly

In [5]:
file_path = "dir_names.txt"  # Ensure this file exists
directory_name = []
with open(file_path, "r") as file:
    directory_name = [line.strip() for line in file]

master_formatted_train_name = []

columns = ["Train_No", "Train_Name", "Station_Name", "Station_Code", "Delay", "Zone"]
df_master = pd.DataFrame(columns=columns)
df_master["Train_No"] = df_master["Train_No"].astype(str)  # Ensure "Train_No" remains a string

t_no=1

for folder in directory_name:
    formatted_train_names = []
    file_path = os.path.join(folder, "fomatted_links.txt")  # Construct file path
    df_category = pd.DataFrame(columns=columns)
    df_category["Train_No"] = df_category["Train_No"].astype(str)  # Ensure "Train_No" remains a string
    i=int(1)
    
    try:
        with open(file_path, "r") as file:
            for line in file: # For each train in that category
                try:
                    line = line.strip() + "?d=1w"
                    print(f"Processing folder {folder} Train Serial No {t_no} : link = {line}")
                    t_no += 1
                    browser.get(line)
                    elements = browser.find_elements(By.CSS_SELECTOR, "td.left.pud3")
                    del elements[1:2]
                    elements.pop()

                    match = re.search(r"Running History of (.+?) \((\d{5})\)", elements[0].text)

                    if match:
                        train_name = match.group(1)  # Extracts the name
                        train_number = str(match.group(2))  # Extracts the number

                    df_train = pd.DataFrame(columns=columns)
                    df_train["Train_No"] = df_train["Train_No"].astype(str)  # Ensure "Train_No" remains a string

                    if(elements[1].text == "Historical running data of queried train for selected duration is not available."):
                        df_train.loc[len(df_train)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                        df_category.loc[len(df_category)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                        df_master.loc[len(df_master)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                    else:
                        del elements[0]
                        sub_elements=elements[0].find_elements(By.CLASS_NAME, "runStatStn")
                        rows = browser.find_elements(By.CSS_SELECTOR, "tr.even.dborder")
                        td_element=rows[2].find_elements(By.CSS_SELECTOR, "td[colspan]")[0].text                        
                        match = re.search(r"Zone:\s*([A-Z]+)", td_element)

                        zone = match.group(1)  # Extracted zone code

                        for sub_element in sub_elements:
                            class_value = sub_element.get_attribute("class")  # Get full class attribute
                            
                            if "runStatStn blocklink rnd5" in class_value:  # Ensure full class match
                                match = re.search(r"([\w\s]+) \((\w+)\)\s*\nAvg\. Delay: (\d+) Min", sub_element.text)

                                if match:
                                    station_name = match.group(1)  # "KANPUR CENTRAL"
                                    station_code = match.group(2)  # "CNB"
                                    delay = match.group(3)         # "56"
                                    df_train.loc[len(df_train)] = [train_number, train_name, station_name, station_code, delay, zone]
                                    df_category.loc[len(df_category)] = [train_number, train_name, station_name, station_code, delay, zone]
                                    df_master.loc[len(df_master)] = [train_number, train_name, station_name, station_code, delay, zone]

                    save_folder = os.path.join(folder, "Weekly_Delay")

                    os.makedirs(save_folder, exist_ok=True)  # Creates "Monthly" inside "folder" if not present

                    save_file_train = os.path.join(save_folder, f"{i}_{train_number}_Weekly_Delay.csv")
                    df_train.to_csv(save_file_train, index=False)  # Saves without index
                    i+=1
                except Exception as e:
                    logging.error(f"Error occurred: {e} in processing link {line}?d=1w", exc_info=True)  # Logs full traceback

        save_file_cat = os.path.join(folder, "Category_Weekly_Delay.csv")
        df_category.to_csv(save_file_cat, index=False)  # Saves without index
    except Exception as e:
        logging.error(f"Error occurred: {e} in category {folder} in week processing", exc_info=True)  # Logs full traceback
    
save_folder = "Master_Delay"
os.makedirs(save_folder, exist_ok=True)
Master_Weekly_Delay_Save = os.path.join(save_folder, "Master_Weekly_Delay.csv")
df_master.to_csv(Master_Weekly_Delay_Save, index=False)

Processing folder List_of_All_Rajdhani_Trains Train Serial No 1 : link = https://etrain.info/train/Nzm-Rajdhani-Spl-01221/history?d=1w
Processing folder List_of_All_Rajdhani_Trains Train Serial No 2 : link = https://etrain.info/train/Csmt-Rajdni-Spl-01222/history?d=1w
Processing folder List_of_All_Rajdhani_Trains Train Serial No 3 : link = https://etrain.info/train/Tvc-Nzm-Raj-Exp-02431/history?d=1w
Processing folder List_of_All_Rajdhani_Trains Train Serial No 4 : link = https://etrain.info/train/Nzm-Tvc-Raj-Spl-02432/history?d=1w
Processing folder List_of_All_Rajdhani_Trains Train Serial No 5 : link = https://etrain.info/train/Ndls-Rnc-Spl-02454/history?d=1w
Processing folder List_of_All_Rajdhani_Trains Train Serial No 6 : link = https://etrain.info/train/Kolkata-Rajdhni-12301/history?d=1w
Processing folder List_of_All_Rajdhani_Trains Train Serial No 7 : link = https://etrain.info/train/Kolkata-Rjdhni-12302/history?d=1w
Processing folder List_of_All_Rajdhani_Trains Train Serial No 8 :

2025-03-08 21:48:21,221 - ERROR - Error occurred: pop from empty list in processing link https://etrain.info/train/Rmr-Cdg-Sf-Exp-12527/history?d=1w?d=1w
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/625798478.py", line 31, in <module>
    elements.pop()
    ~~~~~~~~~~~~^^
IndexError: pop from empty list
2025-03-08 21:48:21,311 - ERROR - Error occurred: pop from empty list in processing link https://etrain.info/train/Cdg-Rmr-Sf-Exp-12528/history?d=1w?d=1w
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/625798478.py", line 31, in <module>
    elements.pop()
    ~~~~~~~~~~~~^^
IndexError: pop from empty list


Processing folder List_of_All_Superfast_Trains Train Serial No 1324 : link = https://etrain.info/train/Rmr-Cdg-Sf-Exp-12527/history?d=1w
Processing folder List_of_All_Superfast_Trains Train Serial No 1325 : link = https://etrain.info/train/Cdg-Rmr-Sf-Exp-12528/history?d=1w
Processing folder List_of_All_Superfast_Trains Train Serial No 1326 : link = https://etrain.info/train/Ppta-Ljn-Sf-Exp-12529/history?d=1w
Processing folder List_of_All_Superfast_Trains Train Serial No 1327 : link = https://etrain.info/train/Ljn-Ppta-Sf-Exp-12530/history?d=1w
Processing folder List_of_All_Superfast_Trains Train Serial No 1328 : link = https://etrain.info/train/Pushpak-Express-12533/history?d=1w
Processing folder List_of_All_Superfast_Trains Train Serial No 1329 : link = https://etrain.info/train/Pushpak-Express-12534/history?d=1w
Processing folder List_of_All_Superfast_Trains Train Serial No 1330 : link = https://etrain.info/train/Manduadih-Exp-12537/history?d=1w
Processing folder List_of_All_Superfas

2025-03-08 22:32:41,681 - ERROR - Error occurred: pop from empty list in processing link https://etrain.info/train/Pnbe-Ssm-Passenger-53211/history?d=1w?d=1w
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/625798478.py", line 31, in <module>
    elements.pop()
    ~~~~~~~~~~~~^^
IndexError: pop from empty list


Processing folder List_of_All_Passenger_Trains Train Serial No 5157 : link = https://etrain.info/train/Ssm-Pnbe-Passenger-53212/history?d=1w
Processing folder List_of_All_Passenger_Trains Train Serial No 5158 : link = https://etrain.info/train/Pnbe-Gaya-Passenger-53213/history?d=1w
Processing folder List_of_All_Passenger_Trains Train Serial No 5159 : link = https://etrain.info/train/Gaya-Pnbe-Passenger-53214/history?d=1w
Processing folder List_of_All_Passenger_Trains Train Serial No 5160 : link = https://etrain.info/train/Bxr-Mgs-Pass-53219/history?d=1w
Processing folder List_of_All_Passenger_Trains Train Serial No 5161 : link = https://etrain.info/train/Rgd-Bkp-Pass-53221/history?d=1w
Processing folder List_of_All_Passenger_Trains Train Serial No 5162 : link = https://etrain.info/train/Bkp-Rgd-Pass-53222/history?d=1w
Processing folder List_of_All_Passenger_Trains Train Serial No 5163 : link = https://etrain.info/train/Rgd-Bkp-Pass-53223/history?d=1w
Processing folder List_of_All_Passe

# 3 Months

In [6]:
file_path = "dir_names.txt"  # Ensure this file exists
directory_name = []
with open(file_path, "r") as file:
    directory_name = [line.strip() for line in file]

master_formatted_train_name = []

columns = ["Train_No", "Train_Name", "Station_Name", "Station_Code", "Delay", "Zone"]
df_master = pd.DataFrame(columns=columns)
df_master["Train_No"] = df_master["Train_No"].astype(str)  # Ensure "Train_No" remains a string

t_no=1

for folder in directory_name:
    formatted_train_names = []
    file_path = os.path.join(folder, "fomatted_links.txt")  # Construct file path
    df_category = pd.DataFrame(columns=columns)
    df_category["Train_No"] = df_category["Train_No"].astype(str)  # Ensure "Train_No" remains a string
    i=int(1)
    
    try:
        with open(file_path, "r") as file:
            for line in file: # For each train in that category
                try:
                    line = line.strip() + "?d=3m"
                    print(f"Processing folder {folder} Train Serial No {t_no} : link = {line}")
                    t_no += 1
                    browser.get(line)
                    elements = browser.find_elements(By.CSS_SELECTOR, "td.left.pud3")
                    del elements[1:2]
                    elements.pop()

                    match = re.search(r"Running History of (.+?) \((\d{5})\)", elements[0].text)

                    if match:
                        train_name = match.group(1)  # Extracts the name
                        train_number = str(match.group(2))  # Extracts the number

                    df_train = pd.DataFrame(columns=columns)
                    df_train["Train_No"] = df_train["Train_No"].astype(str)  # Ensure "Train_No" remains a string

                    if(elements[1].text == "Historical running data of queried train for selected duration is not available."):
                        df_train.loc[len(df_train)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                        df_category.loc[len(df_category)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                        df_master.loc[len(df_master)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                    else:
                        del elements[0]
                        sub_elements=elements[0].find_elements(By.CLASS_NAME, "runStatStn")
                            
                        rows = browser.find_elements(By.CSS_SELECTOR, "tr.even.dborder")    
                        td_element=rows[2].find_elements(By.CSS_SELECTOR, "td[colspan]")[0].text
                        match = re.search(r"Zone:\s*([A-Z]+)", td_element)

                        zone = match.group(1)  # Extracted zone code

                        for sub_element in sub_elements:
                            class_value = sub_element.get_attribute("class")  # Get full class attribute
                            
                            if "runStatStn blocklink rnd5" in class_value:  # Ensure full class match
                                match = re.search(r"([\w\s]+) \((\w+)\)\s*\nAvg\. Delay: (\d+) Min", sub_element.text)

                                if match:
                                    station_name = match.group(1)  # "KANPUR CENTRAL"
                                    station_code = match.group(2)  # "CNB"
                                    delay = match.group(3)         # "56"
                                    
                                    df_train.loc[len(df_train)] = [train_number, train_name, station_name, station_code, delay, zone]
                                    df_category.loc[len(df_category)] = [train_number, train_name, station_name, station_code, delay, zone]
                                    df_master.loc[len(df_master)] = [train_number, train_name, station_name, station_code, delay, zone]
                                    # '''
                    save_folder = os.path.join(folder, "3M_Delay")

                    os.makedirs(save_folder, exist_ok=True)  # Creates "3M" inside "folder" if not present

                    save_file_train = os.path.join(save_folder, f"{i}_{train_number}_3M_Delay.csv")
                    df_train.to_csv(save_file_train, index=False)  # Saves without index
                    i+=1
                except Exception as e:
                    logging.error(f"Error occurred: {e} in processing link {line}?d=3m", exc_info=True)  # Logs full traceback

        save_file_cat = os.path.join(folder, "Category_3M_Delay.csv")
        df_category.to_csv(save_file_cat, index=False)  # Saves without index
    except Exception as e:
        logging.error(f"Error occurred: {e} in category {folder} in 3M processing", exc_info=True)  # Logs full traceback
    
save_folder = "Master_Delay"
os.makedirs(save_folder, exist_ok=True)
Master_3M_Delay_Save = os.path.join(save_folder, "Master_3M_Delay.csv")
df_master.to_csv(Master_3M_Delay_Save, index=False)

Processing folder List_of_All_Rajdhani_Trains Train Serial No 1 : link = https://etrain.info/train/Nzm-Rajdhani-Spl-01221/history?d=3m
Processing folder List_of_All_Rajdhani_Trains Train Serial No 2 : link = https://etrain.info/train/Csmt-Rajdni-Spl-01222/history?d=3m
Processing folder List_of_All_Rajdhani_Trains Train Serial No 3 : link = https://etrain.info/train/Tvc-Nzm-Raj-Exp-02431/history?d=3m
Processing folder List_of_All_Rajdhani_Trains Train Serial No 4 : link = https://etrain.info/train/Nzm-Tvc-Raj-Spl-02432/history?d=3m
Processing folder List_of_All_Rajdhani_Trains Train Serial No 5 : link = https://etrain.info/train/Ndls-Rnc-Spl-02454/history?d=3m
Processing folder List_of_All_Rajdhani_Trains Train Serial No 6 : link = https://etrain.info/train/Kolkata-Rajdhni-12301/history?d=3m
Processing folder List_of_All_Rajdhani_Trains Train Serial No 7 : link = https://etrain.info/train/Kolkata-Rjdhni-12302/history?d=3m
Processing folder List_of_All_Rajdhani_Trains Train Serial No 8 :

2025-03-08 23:26:55,745 - ERROR - Error occurred: pop from empty list in processing link https://etrain.info/train/Rmr-Cdg-Sf-Exp-12527/history?d=3m?d=3m
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/1866304888.py", line 31, in <module>
    elements.pop()
    ~~~~~~~~~~~~^^
IndexError: pop from empty list
2025-03-08 23:26:55,842 - ERROR - Error occurred: pop from empty list in processing link https://etrain.info/train/Cdg-Rmr-Sf-Exp-12528/history?d=3m?d=3m
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/1866304888.py", line 31, in <module>
    elements.pop()
    ~~~~~~~~~~~~^^
IndexError: pop from empty list


Processing folder List_of_All_Superfast_Trains Train Serial No 1324 : link = https://etrain.info/train/Rmr-Cdg-Sf-Exp-12527/history?d=3m
Processing folder List_of_All_Superfast_Trains Train Serial No 1325 : link = https://etrain.info/train/Cdg-Rmr-Sf-Exp-12528/history?d=3m
Processing folder List_of_All_Superfast_Trains Train Serial No 1326 : link = https://etrain.info/train/Ppta-Ljn-Sf-Exp-12529/history?d=3m
Processing folder List_of_All_Superfast_Trains Train Serial No 1327 : link = https://etrain.info/train/Ljn-Ppta-Sf-Exp-12530/history?d=3m
Processing folder List_of_All_Superfast_Trains Train Serial No 1328 : link = https://etrain.info/train/Pushpak-Express-12533/history?d=3m
Processing folder List_of_All_Superfast_Trains Train Serial No 1329 : link = https://etrain.info/train/Pushpak-Express-12534/history?d=3m
Processing folder List_of_All_Superfast_Trains Train Serial No 1330 : link = https://etrain.info/train/Manduadih-Exp-12537/history?d=3m
Processing folder List_of_All_Superfas

2025-03-08 23:39:38,879 - ERROR - Error occurred: 'NoneType' object has no attribute 'group' in processing link https://etrain.info/train/Gct-Sdah-Spl-05092/history?d=3m?d=3m
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/1866304888.py", line 54, in <module>
    zone = match.group(1)  # Extracted zone code
           ^^^^^^^^^^^
AttributeError: 'NoneType' object has no attribute 'group'


Processing folder List_of_All_Mail/Express_Trains Train Serial No 2528 : link = https://etrain.info/train/Cpr-Ghy-Spl-05094/history?d=3m


2025-03-08 23:39:39,107 - ERROR - Error occurred: 'NoneType' object has no attribute 'group' in processing link https://etrain.info/train/Cpr-Ghy-Spl-05094/history?d=3m?d=3m
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/1866304888.py", line 54, in <module>
    zone = match.group(1)  # Extracted zone code
           ^^^^^^^^^^^
AttributeError: 'NoneType' object has no attribute 'group'


Processing folder List_of_All_Mail/Express_Trains Train Serial No 2529 : link = https://etrain.info/train/Amh-Sc-Spl-05096/history?d=3m


2025-03-08 23:39:39,328 - ERROR - Error occurred: 'NoneType' object has no attribute 'group' in processing link https://etrain.info/train/Amh-Sc-Spl-05096/history?d=3m?d=3m
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/1866304888.py", line 54, in <module>
    zone = match.group(1)  # Extracted zone code
           ^^^^^^^^^^^
AttributeError: 'NoneType' object has no attribute 'group'


Processing folder List_of_All_Mail/Express_Trains Train Serial No 2530 : link = https://etrain.info/train/Tpu-Doz-Spl-05097/history?d=3m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2531 : link = https://etrain.info/train/Doz-Tpu-Spl-05098/history?d=3m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2532 : link = https://etrain.info/train/Cpr-Anvt-Special-05113/history?d=3m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2533 : link = https://etrain.info/train/Cpr-Holi-Spl-05114/history?d=3m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2534 : link = https://etrain.info/train/The-Ci-Exp-Spl-05121/history?d=3m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2535 : link = https://etrain.info/train/Ci-The-Exp-Spl-05122/history?d=3m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2536 : link = https://etrain.info/train/Gkp-Brk-Spl-05131/history?d=3m
Processing folder List_of_All

# 6 Months

In [7]:
file_path = "dir_names.txt"  # Ensure this file exists

directory_name = []
with open(file_path, "r") as file:
    directory_name = [line.strip() for line in file]

master_formatted_train_name = []

columns = ["Train_No", "Train_Name", "Station_Name", "Station_Code", "Delay", "Zone"]
df_master = pd.DataFrame(columns=columns)
df_master["Train_No"] = df_master["Train_No"].astype(str)  # Ensure "Train_No" remains a string

t_no=1

for folder in directory_name:
    formatted_train_names = []
    file_path = os.path.join(folder, "fomatted_links.txt")  # Construct file path
    df_category = pd.DataFrame(columns=columns)
    df_category["Train_No"] = df_category["Train_No"].astype(str)  # Ensure "Train_No" remains a string
    i=int(1)
    
    try:
        with open(file_path, "r") as file:
            for line in file: # For each train in that category
                try:
                    line = line.strip() + "?d=6m"
                    print(f"Processing folder {folder} Train Serial No {t_no} : link = {line}")
                    t_no += 1

                    browser.get(line)

                    elements = browser.find_elements(By.CSS_SELECTOR, "td.left.pud3")
                    del elements[1:2]
                    elements.pop()

                    match = re.search(r"Running History of (.+?) \((\d{5})\)", elements[0].text)

                    if match:
                        train_name = match.group(1)  # Extracts the name
                        train_number = str(match.group(2))  # Extracts the number

                    df_train = pd.DataFrame(columns=columns)
                    df_train["Train_No"] = df_train["Train_No"].astype(str)  # Ensure "Train_No" remains a string

                    if(elements[1].text == "Historical running data of queried train for selected duration is not available."):
                        df_train.loc[len(df_train)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                        df_category.loc[len(df_category)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                        df_master.loc[len(df_master)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                    else:
                        del elements[0]
                        sub_elements=elements[0].find_elements(By.CLASS_NAME, "runStatStn")
                            
                            
                        rows = browser.find_elements(By.CSS_SELECTOR, "tr.even.dborder")
    
                        td_element=rows[2].find_elements(By.CSS_SELECTOR, "td[colspan]")[0].text
                        
                        match = re.search(r"Zone:\s*([A-Z]+)", td_element)

                        zone = match.group(1)  # Extracted zone code

                        for sub_element in sub_elements:
                            class_value = sub_element.get_attribute("class")  # Get full class attribute
                            
                            if "runStatStn blocklink rnd5" in class_value:  # Ensure full class match
                                match = re.search(r"([\w\s]+) \((\w+)\)\s*\nAvg\. Delay: (\d+) Min", sub_element.text)

                                if match:
                                    station_name = match.group(1)  # "KANPUR CENTRAL"
                                    station_code = match.group(2)  # "CNB"
                                    delay = match.group(3)         # "56"
                                    
                                    df_train.loc[len(df_train)] = [train_number, train_name, station_name, station_code, delay, zone]
                                    df_category.loc[len(df_category)] = [train_number, train_name, station_name, station_code, delay, zone]
                                    df_master.loc[len(df_master)] = [train_number, train_name, station_name, station_code, delay, zone]
                    
                    save_folder = os.path.join(folder, "6M_Delay")

                    os.makedirs(save_folder, exist_ok=True)  # Creates "6M" inside "folder" if not present

                    save_file_train = os.path.join(save_folder, f"{i}_{train_number}_6M_Delay.csv")
                    df_train.to_csv(save_file_train, index=False)  # Saves without index

                    i+=1
                except Exception as e:
                    logging.error(f"Error occurred: {e} in processing link {line}", exc_info=True)  # Logs full traceback

        save_file_cat = os.path.join(folder, "Category_6M_Delay.csv")
        df_category.to_csv(save_file_cat, index=False)  # Saves without index
    except Exception as e:
        logging.error(f"Error occurred: {e} in category {folder} in 6M processing", exc_info=True)  # Logs full traceback
    
save_folder = "Master_Delay"
os.makedirs(save_folder, exist_ok=True)
Master_6M_Delay_Save = os.path.join(save_folder, "Master_6M_Delay.csv")
df_master.to_csv(Master_6M_Delay_Save, index=False)

Processing folder List_of_All_Rajdhani_Trains Train Serial No 1 : link = https://etrain.info/train/Nzm-Rajdhani-Spl-01221/history?d=6m
Processing folder List_of_All_Rajdhani_Trains Train Serial No 2 : link = https://etrain.info/train/Csmt-Rajdni-Spl-01222/history?d=6m
Processing folder List_of_All_Rajdhani_Trains Train Serial No 3 : link = https://etrain.info/train/Tvc-Nzm-Raj-Exp-02431/history?d=6m
Processing folder List_of_All_Rajdhani_Trains Train Serial No 4 : link = https://etrain.info/train/Nzm-Tvc-Raj-Spl-02432/history?d=6m
Processing folder List_of_All_Rajdhani_Trains Train Serial No 5 : link = https://etrain.info/train/Ndls-Rnc-Spl-02454/history?d=6m
Processing folder List_of_All_Rajdhani_Trains Train Serial No 6 : link = https://etrain.info/train/Kolkata-Rajdhni-12301/history?d=6m
Processing folder List_of_All_Rajdhani_Trains Train Serial No 7 : link = https://etrain.info/train/Kolkata-Rjdhni-12302/history?d=6m
Processing folder List_of_All_Rajdhani_Trains Train Serial No 8 :

2025-03-09 01:15:10,205 - ERROR - Error occurred: pop from empty list in processing link https://etrain.info/train/Rmr-Cdg-Sf-Exp-12527/history?d=6m
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/3718007510.py", line 34, in <module>
    elements.pop()
    ~~~~~~~~~~~~^^
IndexError: pop from empty list
2025-03-09 01:15:10,298 - ERROR - Error occurred: pop from empty list in processing link https://etrain.info/train/Cdg-Rmr-Sf-Exp-12528/history?d=6m
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/3718007510.py", line 34, in <module>
    elements.pop()
    ~~~~~~~~~~~~^^
IndexError: pop from empty list


Processing folder List_of_All_Superfast_Trains Train Serial No 1324 : link = https://etrain.info/train/Rmr-Cdg-Sf-Exp-12527/history?d=6m
Processing folder List_of_All_Superfast_Trains Train Serial No 1325 : link = https://etrain.info/train/Cdg-Rmr-Sf-Exp-12528/history?d=6m
Processing folder List_of_All_Superfast_Trains Train Serial No 1326 : link = https://etrain.info/train/Ppta-Ljn-Sf-Exp-12529/history?d=6m
Processing folder List_of_All_Superfast_Trains Train Serial No 1327 : link = https://etrain.info/train/Ljn-Ppta-Sf-Exp-12530/history?d=6m
Processing folder List_of_All_Superfast_Trains Train Serial No 1328 : link = https://etrain.info/train/Pushpak-Express-12533/history?d=6m
Processing folder List_of_All_Superfast_Trains Train Serial No 1329 : link = https://etrain.info/train/Pushpak-Express-12534/history?d=6m
Processing folder List_of_All_Superfast_Trains Train Serial No 1330 : link = https://etrain.info/train/Manduadih-Exp-12537/history?d=6m
Processing folder List_of_All_Superfas

2025-03-09 01:27:36,468 - ERROR - Error occurred: 'NoneType' object has no attribute 'group' in processing link https://etrain.info/train/Koaa-Jyg-Spl-03187/history?d=6m
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/3718007510.py", line 60, in <module>
    zone = match.group(1)  # Extracted zone code
           ^^^^^^^^^^^
AttributeError: 'NoneType' object has no attribute 'group'


Processing folder List_of_All_Mail/Express_Trains Train Serial No 2408 : link = https://etrain.info/train/Koaa-Jyg-Spl-03187/history?d=6m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2409 : link = https://etrain.info/train/Jyg-Koaa-Spl-03188/history?d=6m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2410 : link = https://etrain.info/train/Pnbe-The-Express-Spl-03215/history?d=6m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2411 : link = https://etrain.info/train/The-Pnbe-Express-Spl-03216/history?d=6m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2412 : link = https://etrain.info/train/Puri-Pnbe-Spl-03229/history?d=6m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2413 : link = https://etrain.info/train/Pnbe-Puri-Spl-03230/history?d=6m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2414 : link = https://etrain.info/train/Rgd-Pnbe-Spl-03249/history?d=6m
Processing folde

...

Processing folder List_of_All_Mail/Express_Trains Train Serial No 2528 : link = https://etrain.info/train/Cpr-Ghy-Spl-05094/history?d=6m


2025-03-09 01:28:50,360 - ERROR - Error occurred: 'NoneType' object has no attribute 'group' in processing link https://etrain.info/train/Cpr-Ghy-Spl-05094/history?d=6m
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/3718007510.py", line 60, in <module>
    zone = match.group(1)  # Extracted zone code
           ^^^^^^^^^^^
AttributeError: 'NoneType' object has no attribute 'group'


Processing folder List_of_All_Mail/Express_Trains Train Serial No 2529 : link = https://etrain.info/train/Amh-Sc-Spl-05096/history?d=6m


2025-03-09 01:28:50,718 - ERROR - Error occurred: 'NoneType' object has no attribute 'group' in processing link https://etrain.info/train/Amh-Sc-Spl-05096/history?d=6m
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/3718007510.py", line 60, in <module>
    zone = match.group(1)  # Extracted zone code
           ^^^^^^^^^^^
AttributeError: 'NoneType' object has no attribute 'group'


Processing folder List_of_All_Mail/Express_Trains Train Serial No 2530 : link = https://etrain.info/train/Tpu-Doz-Spl-05097/history?d=6m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2531 : link = https://etrain.info/train/Doz-Tpu-Spl-05098/history?d=6m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2532 : link = https://etrain.info/train/Cpr-Anvt-Special-05113/history?d=6m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2533 : link = https://etrain.info/train/Cpr-Holi-Spl-05114/history?d=6m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2534 : link = https://etrain.info/train/The-Ci-Exp-Spl-05121/history?d=6m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2535 : link = https://etrain.info/train/Ci-The-Exp-Spl-05122/history?d=6m
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2536 : link = https://etrain.info/train/Gkp-Brk-Spl-05131/history?d=6m
Processing folder List_of_All

# Year

In [8]:
file_path = "dir_names.txt"  # Ensure this file exists

directory_name = []
with open(file_path, "r") as file:
    directory_name = [line.strip() for line in file]

master_formatted_train_name = []

columns = ["Train_No", "Train_Name", "Station_Name", "Station_Code", "Delay", "Zone"]
df_master = pd.DataFrame(columns=columns)
df_master["Train_No"] = df_master["Train_No"].astype(str)  # Ensure "Train_No" remains a string

t_no = 1

for folder in directory_name:
    formatted_train_names = []
    file_path = os.path.join(folder, "fomatted_links.txt")  # Construct file path
    df_category = pd.DataFrame(columns=columns)
    df_category["Train_No"] = df_category["Train_No"].astype(str)  # Ensure "Train_No" remains a string
    i=int(1)
    
    try:
        with open(file_path, "r") as file:
            for line in file: # For each train in that category
                try:
                    line = line.strip() + "?d=1y"
                    print(f"Processing folder {folder} Train Serial No {t_no} : link = {line}")
                    t_no += 1
                    browser.get(line)
                    elements = browser.find_elements(By.CSS_SELECTOR, "td.left.pud3")
                    del elements[1:2]
                    elements.pop()

                    match = re.search(r"Running History of (.+?) \((\d{5})\)", elements[0].text)

                    if match:
                        train_name = match.group(1)  # Extracts the name
                        train_number = str(match.group(2))  # Extracts the number

                    df_train = pd.DataFrame(columns=columns)
                    df_train["Train_No"] = df_train["Train_No"].astype(str)  # Ensure "Train_No" remains a string

                    if(elements[1].text == "Historical running data of queried train for selected duration is not available."):
                        df_train.loc[len(df_train)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                        df_category.loc[len(df_category)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                        df_master.loc[len(df_master)] = [train_number, train_name, pd.NA, pd.NA, pd.NA, pd.NA]
                    else:
                        del elements[0]
                        sub_elements=elements[0].find_elements(By.CLASS_NAME, "runStatStn")
                            
                        rows = browser.find_elements(By.CSS_SELECTOR, "tr.even.dborder")
                        td_element=rows[2].find_elements(By.CSS_SELECTOR, "td[colspan]")[0].text
                        
                        match = re.search(r"Zone:\s*([A-Z]+)", td_element)
                            
                        zone = match.group(1)  # Extracted zone code

                        for sub_element in sub_elements:
                            class_value = sub_element.get_attribute("class")  # Get full class attribute
                                                        
                            if "runStatStn blocklink rnd5" in class_value:  # Ensure full class match
                                match = re.search(r"([\w\s]+) \((\w+)\)\s*\nAvg\. Delay: (\d+) Min", sub_element.text)

                                if match:
                                    station_name = match.group(1)  # "KANPUR CENTRAL"
                                    station_code = match.group(2)  # "CNB"
                                    delay = match.group(3)         # "56"
                                    
                                    df_train.loc[len(df_train)] = [train_number, train_name, station_name, station_code, delay, zone]
                                    df_category.loc[len(df_category)] = [train_number, train_name, station_name, station_code, delay, zone]
                                    df_master.loc[len(df_master)] = [train_number, train_name, station_name, station_code, delay, zone]
                    save_folder = os.path.join(folder, "Yearly_Delay")

                    os.makedirs(save_folder, exist_ok=True)  # Creates "Yearly" inside "folder" if not present

                    save_file_train = os.path.join(save_folder, f"{i}_{train_number}_Yearly_Delay.csv")
                    df_train.to_csv(save_file_train, index=False)  # Saves without index
                    i+=1
                except Exception as e:
                    logging.error(f"Error occurred: {e} in processing link {line}", exc_info=True)  # Logs full traceback


        save_file_cat = os.path.join(folder, "Category_Yearly_Delay.csv")
        df_category.to_csv(save_file_cat, index=False)  # Saves without index
    except Exception as e:
        logging.error(f"Error occurred: {e} in category {folder} in Yearly processing", exc_info=True)  # Logs full traceback
    
save_folder = "Master_Delay"
os.makedirs(save_folder, exist_ok=True)
Master_Yearly_Delay_Save = os.path.join(save_folder, "Master_Yearly_Delay.csv")
df_master.to_csv(Master_Yearly_Delay_Save, index=False)

Processing folder List_of_All_Rajdhani_Trains Train Serial No 1 : link = https://etrain.info/train/Nzm-Rajdhani-Spl-01221/history?d=1y
Processing folder List_of_All_Rajdhani_Trains Train Serial No 2 : link = https://etrain.info/train/Csmt-Rajdni-Spl-01222/history?d=1y
Processing folder List_of_All_Rajdhani_Trains Train Serial No 3 : link = https://etrain.info/train/Tvc-Nzm-Raj-Exp-02431/history?d=1y
Processing folder List_of_All_Rajdhani_Trains Train Serial No 4 : link = https://etrain.info/train/Nzm-Tvc-Raj-Spl-02432/history?d=1y
Processing folder List_of_All_Rajdhani_Trains Train Serial No 5 : link = https://etrain.info/train/Ndls-Rnc-Spl-02454/history?d=1y
Processing folder List_of_All_Rajdhani_Trains Train Serial No 6 : link = https://etrain.info/train/Kolkata-Rajdhni-12301/history?d=1y
Processing folder List_of_All_Rajdhani_Trains Train Serial No 7 : link = https://etrain.info/train/Kolkata-Rjdhni-12302/history?d=1y
Processing folder List_of_All_Rajdhani_Trains Train Serial No 8 :

2025-03-09 02:54:12,298 - ERROR - Error occurred: 'NoneType' object has no attribute 'group' in processing link https://etrain.info/train/Indb-Holi-Spl-04412/history?d=1y
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/3503649374.py", line 56, in <module>
    zone = match.group(1)  # Extracted zone code
           ^^^^^^^^^^^
AttributeError: 'NoneType' object has no attribute 'group'


Processing folder List_of_All_Superfast_Trains Train Serial No 983 : link = https://etrain.info/train/Indb-Holi-Spl-04412/history?d=1y
Processing folder List_of_All_Superfast_Trains Train Serial No 984 : link = https://etrain.info/train/Mfp-Anvt-Sf-Spl-05219/history?d=1y
Processing folder List_of_All_Superfast_Trains Train Serial No 985 : link = https://etrain.info/train/Mfp-Sf-Holi-Spl-05220/history?d=1y
Processing folder List_of_All_Superfast_Trains Train Serial No 986 : link = https://etrain.info/train/Mfp-Pune-Ac-Spl-05289/history?d=1y
Processing folder List_of_All_Superfast_Trains Train Serial No 987 : link = https://etrain.info/train/Pune-Mfp-Sf-Spl-05290/history?d=1y
Processing folder List_of_All_Superfast_Trains Train Serial No 988 : link = https://etrain.info/train/Tbm-Ncj-Sf-Spl-06011/history?d=1y
Processing folder List_of_All_Superfast_Trains Train Serial No 989 : link = https://etrain.info/train/Ncj-Tbm-Sf-Spl-06012/history?d=1y
Processing folder List_of_All_Superfast_Train

2025-03-09 02:57:41,740 - ERROR - Error occurred: pop from empty list in processing link https://etrain.info/train/Rmr-Cdg-Sf-Exp-12527/history?d=1y
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/3503649374.py", line 32, in <module>
    elements.pop()
    ~~~~~~~~~~~~^^
IndexError: pop from empty list


Processing folder List_of_All_Superfast_Trains Train Serial No 1324 : link = https://etrain.info/train/Rmr-Cdg-Sf-Exp-12527/history?d=1y
Processing folder List_of_All_Superfast_Trains Train Serial No 1325 : link = https://etrain.info/train/Cdg-Rmr-Sf-Exp-12528/history?d=1y


...

Processing folder List_of_All_Mail/Express_Trains Train Serial No 2528 : link = https://etrain.info/train/Cpr-Ghy-Spl-05094/history?d=1y


2025-03-09 03:11:05,816 - ERROR - Error occurred: 'NoneType' object has no attribute 'group' in processing link https://etrain.info/train/Cpr-Ghy-Spl-05094/history?d=1y
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/3503649374.py", line 56, in <module>
    zone = match.group(1)  # Extracted zone code
           ^^^^^^^^^^^
AttributeError: 'NoneType' object has no attribute 'group'


Processing folder List_of_All_Mail/Express_Trains Train Serial No 2529 : link = https://etrain.info/train/Amh-Sc-Spl-05096/history?d=1y


2025-03-09 03:11:06,066 - ERROR - Error occurred: 'NoneType' object has no attribute 'group' in processing link https://etrain.info/train/Amh-Sc-Spl-05096/history?d=1y
Traceback (most recent call last):
  File "/tmp/ipykernel_73654/3503649374.py", line 56, in <module>
    zone = match.group(1)  # Extracted zone code
           ^^^^^^^^^^^
AttributeError: 'NoneType' object has no attribute 'group'


Processing folder List_of_All_Mail/Express_Trains Train Serial No 2530 : link = https://etrain.info/train/Tpu-Doz-Spl-05097/history?d=1y
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2531 : link = https://etrain.info/train/Doz-Tpu-Spl-05098/history?d=1y
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2532 : link = https://etrain.info/train/Cpr-Anvt-Special-05113/history?d=1y
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2533 : link = https://etrain.info/train/Cpr-Holi-Spl-05114/history?d=1y
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2534 : link = https://etrain.info/train/The-Ci-Exp-Spl-05121/history?d=1y
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2535 : link = https://etrain.info/train/Ci-The-Exp-Spl-05122/history?d=1y
Processing folder List_of_All_Mail/Express_Trains Train Serial No 2536 : link = https://etrain.info/train/Gkp-Brk-Spl-05131/history?d=1y
Processing folder List_of_All

In [ ]:
print(folder)

In [ ]:
train_number

In [ ]:
# browser.quit()